 ### Data Ingestion

In [1]:
### Document Structure

from langchain_core.documents import Document
from langchain_community.document_loaders import TextLoader, DirectoryLoader, PyMuPDFLoader, PyPDFLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter
from pathlib import Path

a:\Github\Projects\RAG\.venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
### Some necessary libraries

import numpy as np
from sentence_transformers import SentenceTransformer
import chromadb
from chromadb.config import Settings
import uuid
from typing import Dict, List, Any, Tuple
from sklearn.metrics.pairwise import cosine_similarity
from typing import List, Dict, Any
import time
import os

### Experimenting with functions to learn

In [3]:
doc = Document(
    page_content="This is the main text content and I am using to create the RAG", 
    metadata={"source":"web", 
                         "pages":1,
                         "author":"Reshu",
                         "date_created":"2025-01-01"}
            )
doc

Document(metadata={'source': 'web', 'pages': 1, 'author': 'Reshu', 'date_created': '2025-01-01'}, page_content='This is the main text content and I am using to create the RAG')

In [172]:
# Creating a simple txt file

os.makedirs("../data/text_files", exist_ok=True)

In [173]:
sample_texts={
    "../data/text_files/python_intro.txt":"""Python Programming Introduction

Python is a high-level, interpreted programming language known for its simplicity and readability.
Created by Guido van Rossum and first released in 1991, Python has become one of the most popular
programming languages in the world.

Key Features:
- Easy to learn and use
- Extensive standard library
- Cross-platform compatibility
- Strong community support

Python is widely used in web development, data science, artificial intelligence, and automation.""",
    
    "../data/text_files/machine_learning.txt": """Machine Learning Basics

Machine learning is a subset of artificial intelligence that enables systems to learn and improve
from experience without being explicitly programmed. It focuses on developing computer programs
that can access data and use it to learn for themselves.

Types of Machine Learning:
1. Supervised Learning: Learning with labeled data
2. Unsupervised Learning: Finding patterns in unlabeled data
3. Reinforcement Learning: Learning through rewards and penalties

Applications include image recognition, speech processing, and recommendation systems
    
    
    """

}

for filepath,content in sample_texts.items():
    with open(filepath,'w',encoding="utf-8") as f:
        f.write(content)

print("Sample file created!")

Sample file created!


In [174]:
### TextLoader

loader = TextLoader("../data/text_files/python_intro.txt", encoding="utf-8")

In [175]:
document = loader.load()

In [176]:
print(document)

[Document(metadata={'source': '../data/text_files/python_intro.txt'}, page_content='Python Programming Introduction\n\nPython is a high-level, interpreted programming language known for its simplicity and readability.\nCreated by Guido van Rossum and first released in 1991, Python has become one of the most popular\nprogramming languages in the world.\n\nKey Features:\n- Easy to learn and use\n- Extensive standard library\n- Cross-platform compatibility\n- Strong community support\n\nPython is widely used in web development, data science, artificial intelligence, and automation.')]


In [177]:
### Directory Loader

dir_loader = DirectoryLoader("../data/text_files",
                             glob="**/*.txt",  # Pattern Matching
                             loader_cls=TextLoader,
                             loader_kwargs={'encoding':'utf-8'},
                             show_progress=False
                            )

In [178]:
documents = dir_loader.load()

In [179]:
documents

[Document(metadata={'source': '..\\data\\text_files\\machine_learning.txt'}, page_content='Machine Learning Basics\n\nMachine learning is a subset of artificial intelligence that enables systems to learn and improve\nfrom experience without being explicitly programmed. It focuses on developing computer programs\nthat can access data and use it to learn for themselves.\n\nTypes of Machine Learning:\n1. Supervised Learning: Learning with labeled data\n2. Unsupervised Learning: Finding patterns in unlabeled data\n3. Reinforcement Learning: Learning through rewards and penalties\n\nApplications include image recognition, speech processing, and recommendation systems\n\n\n    '),
 Document(metadata={'source': '..\\data\\text_files\\python_intro.txt'}, page_content='Python Programming Introduction\n\nPython is a high-level, interpreted programming language known for its simplicity and readability.\nCreated by Guido van Rossum and first released in 1991, Python has become one of the most popu

In [180]:
## PDF Loader

dir_loader = DirectoryLoader("../data/pdf",
                             glob="**/*.pdf",  # Pattern Matching
                             loader_cls=PyMuPDFLoader,
                             show_progress=False
                            )

In [181]:
pdf_documents =dir_loader.load()

In [182]:
pdf_documents

[Document(metadata={'producer': 'Microsoft® Word for Microsoft 365', 'creator': 'Microsoft® Word for Microsoft 365', 'creationdate': '2025-09-09T18:53:41+02:00', 'source': '..\\data\\pdf\\The Inner Workings of Large Language Models - How Neural Networks Learn Language.pdf', 'file_path': '..\\data\\pdf\\The Inner Workings of Large Language Models - How Neural Networks Learn Language.pdf', 'total_pages': 67, 'format': 'PDF 1.7', 'title': '', 'author': 'Roger Gullhaug', 'subject': '', 'keywords': '', 'moddate': '2025-09-09T18:53:41+02:00', 'trapped': '', 'modDate': "D:20250909185341+02'00'", 'creationDate': "D:20250909185341+02'00'", 'page': 0}, page_content='The inner workings of Large Language Models \nRoger Gullhaug \n1 \n 1'),
 Document(metadata={'producer': 'Microsoft® Word for Microsoft 365', 'creator': 'Microsoft® Word for Microsoft 365', 'creationdate': '2025-09-09T18:53:41+02:00', 'source': '..\\data\\pdf\\The Inner Workings of Large Language Models - How Neural Networks Learn La

In [183]:
type(pdf_documents[0])

langchain_core.documents.base.Document

### PDF Reader

In [4]:
# Read all the pdf's inside the directory

def process_all_pdfs(pdf_directory):
    """Process all PDF files in a directory"""
    all_documents = []
    pdf_dir = Path(pdf_directory)
    
    # Find all PDF files recursively
    pdf_files = list(pdf_dir.glob("**/*.pdf"))
    
    print(f"Found {len(pdf_files)} PDF files to process")
    
    for pdf_file in pdf_files:
        print(f"\nProcessing: {pdf_file.name}")
        try:
            loader = PyPDFLoader(str(pdf_file))
            documents = loader.load()
            
            # Add source information to metadata
            for doc in documents:
                doc.metadata['source_file'] = pdf_file.name
                doc.metadata['file_type'] = 'pdf'
            
            all_documents.extend(documents)
            print(f"Loaded {len(documents)} pages")
            
        except Exception    as e:
            print(f"Error: {e}")
    
    print(f"\nTotal documents loaded: {len(all_documents)}")
    return all_documents

# Process all PDFs in the data directory
all_pdf_documents = process_all_pdfs("../data")

Found 2 PDF files to process

Processing: The Inner Workings of Large Language Models - How Neural Networks Learn Language.pdf
Loaded 67 pages

Processing: Trading For Dummies.pdf
Loaded 387 pages

Total documents loaded: 454


In [5]:
# Text splitting to get into chunks

def split_documents(documents,chunk_size=1000,chunk_overlap=200):
    """Split documents into smaller chunks"""
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=chunk_size,
        chunk_overlap=chunk_overlap,
        length_function=len,
        separators=["\n\n", "\n", " ", ""]
    )
    split_docs = text_splitter.split_documents(documents)
    print(f"Split {len(documents)} documents into {len(split_docs)} chunks")
    
    return split_docs

In [6]:
chunks=split_documents(all_pdf_documents)
chunks

Split 454 documents into 1293 chunks


[Document(metadata={'producer': 'Microsoft® Word for Microsoft 365', 'creator': 'Microsoft® Word for Microsoft 365', 'creationdate': '2025-09-09T18:53:41+02:00', 'author': 'Roger Gullhaug', 'moddate': '2025-09-09T18:53:41+02:00', 'source': '..\\data\\pdf\\The Inner Workings of Large Language Models - How Neural Networks Learn Language.pdf', 'total_pages': 67, 'page': 0, 'page_label': '1', 'source_file': 'The Inner Workings of Large Language Models - How Neural Networks Learn Language.pdf', 'file_type': 'pdf'}, page_content='The inner workings of Large Language Models Roger Gullhaug \n1 \n \n1'),
 Document(metadata={'producer': 'Microsoft® Word for Microsoft 365', 'creator': 'Microsoft® Word for Microsoft 365', 'creationdate': '2025-09-09T18:53:41+02:00', 'author': 'Roger Gullhaug', 'moddate': '2025-09-09T18:53:41+02:00', 'source': '..\\data\\pdf\\The Inner Workings of Large Language Models - How Neural Networks Learn Language.pdf', 'total_pages': 67, 'page': 1, 'page_label': '2', 'sour

In [7]:
class EmbeddingManager:
    "Handle document embedding generation using sentence/transformer"
    def __init__(self, model_name: str = "all-MiniLM-L6-v2"):
        """Initialize emedding manager
        
        Args:
            model_name: huggingface model name for sentence embeddings 
        
        """
        self.model_name = model_name
        self.model = None
        self._load_model()
    

    def _load_model(self):
        """Loading sentence transformer model"""
        try:
            print(f"loading embedding model: {self.model_name}")
            self.model = SentenceTransformer(self.model_name)
            print(f"model loaded successfully. Embedding Dimension: {self.model.get_sentence_embedding_dimension()}")
        except Exception as e:
            print(f"Error Loading Model {self.model_name}:{e}")
            raise
    

    def generate_embeddings(self, texts: List[str]) -> np.ndarray:
        """
            Generate embeddings for a list of texts

            Args:
                text: list of text strings to embed
            Returns:
                numpy array of embeddings with shape (len(texts), embedding_dim)
        """
        if not self.model:
            raise ValueError("model not loaded")
        
        print(f"Generating Embedding for {len(texts)} texts...")
        embeddings = self.model.encode(texts, show_progress_bar=True)
        print(f"generated embedding with shape: {embeddings.shape}")
        return embeddings

    def get_sentence_embedding_dimension(self) -> int:
        """get the embedding dimension of the model"""
        if not self.model:
            raise ValueError("Model Not Loaded")
        return self.model.get_sentence_embedding_dimension()
    
### initialize the embedding manager
embedding_manager = EmbeddingManager()
embedding_manager

loading embedding model: all-MiniLM-L6-v2
model loaded successfully. Embedding Dimension: 384


In [8]:
### Vector Store

class VectorStore:
    """Manages document embedding in a ChromaDB vector store"""

    def __init__(self, collection_name: str ="pdf_documents", persist_directory: str = "../data/vector_store"):
        """
        Initializing the vector store

        Args:
            collection_name: Name of DBS collection
            persist_directory: Directory to persist vector store
        """
        self.collection_name = collection_name
        self.persist_directory = persist_directory
        self.client = None
        self.collection = None
        self._initialize_store()
    

    def _initialize_store(self):
        """Initialize ChromaDB client and collection"""
        try:
            # Create persistent ChromaDB client
            os.makedirs(self.persist_directory, exist_ok=True)
            self.client = chromadb.PersistentClient(path=self.persist_directory)
            
            # Get or create collection
            self.collection = self.client.get_or_create_collection(
                name=self.collection_name,
                metadata={"description": "PDF document embeddings for RAG"}
            )
            print(f"Vector store initialized. Collection: {self.collection_name}")
            print(f"Existing documents in collection: {self.collection.count()}")
            
        except Exception as e:
            print(f"Error initializing vector store: {e}")
            raise

    def add_documents(self, documents: List[Any], embeddings: np.ndarray):
        """
        Add documents and their embeddings to the vector store
        
        Args:
            documents: List of LangChain documents
            embeddings: Corresponding embeddings for the documents
        """
        if len(documents) != len(embeddings):
            raise ValueError("Number of documents must match number of embeddings")
        
        print(f"Adding {len(documents)} documents to vector store...")
        
        # Prepare data for ChromaDB
        ids = []    
        metadatas = []
        documents_text = []
        embeddings_list = []
        
        for i, (doc, embedding) in enumerate(zip(documents, embeddings)):
            # Generate unique ID
            doc_id = f"doc_{uuid.uuid4().hex[:8]}_{i}"
            ids.append(doc_id)
            
            # Prepare metadata
            metadata = dict(doc.metadata)
            metadata['doc_index'] = i
            metadata['content_length'] = len(doc.page_content)
            metadatas.append(metadata)
            
            # Document content
            documents_text.append(doc.page_content)
            
            # Embedding
            embeddings_list.append(embedding.tolist())
        
        # Add to collection
        try:
            self.collection.add(
                ids=ids,
                embeddings=embeddings_list,
                metadatas=metadatas,
                documents=documents_text
            )
            print(f"Successfully added {len(documents)} documents to vector store")
            print(f"Total documents in collection: {self.collection.count()}")
            
        except Exception as e:
            print(f"Error adding documents to vector store: {e}")
            raise

vectorstore = VectorStore()
vectorstore

Vector store initialized. Collection: pdf_documents
Existing documents in collection: 1271


In [9]:
chunks

[Document(metadata={'producer': 'Microsoft® Word for Microsoft 365', 'creator': 'Microsoft® Word for Microsoft 365', 'creationdate': '2025-09-09T18:53:41+02:00', 'author': 'Roger Gullhaug', 'moddate': '2025-09-09T18:53:41+02:00', 'source': '..\\data\\pdf\\The Inner Workings of Large Language Models - How Neural Networks Learn Language.pdf', 'total_pages': 67, 'page': 0, 'page_label': '1', 'source_file': 'The Inner Workings of Large Language Models - How Neural Networks Learn Language.pdf', 'file_type': 'pdf'}, page_content='The inner workings of Large Language Models Roger Gullhaug \n1 \n \n1'),
 Document(metadata={'producer': 'Microsoft® Word for Microsoft 365', 'creator': 'Microsoft® Word for Microsoft 365', 'creationdate': '2025-09-09T18:53:41+02:00', 'author': 'Roger Gullhaug', 'moddate': '2025-09-09T18:53:41+02:00', 'source': '..\\data\\pdf\\The Inner Workings of Large Language Models - How Neural Networks Learn Language.pdf', 'total_pages': 67, 'page': 1, 'page_label': '2', 'sour

In [10]:
## convert text to embeddings

texts = [doc.page_content for doc in chunks]
texts

['The inner workings of Large Language Models Roger Gullhaug \n1 \n \n1',
 'The inner workings of Large Language Models Roger Gullhaug \n2 \n \n \nCopyright © 2025 Roger Gullhaug. All rights reserved. \n \nNo part of this publication may be reproduced, distributed, or transmitted in any form or \nby any means, including photocopying, recording, scanning, or other electronic or \nmechanical methods, without the prior written permission of the author, except for brief \nquotations used in reviews and certain other uses permitted by copyright law. \n \nFor permissions, contact the author \n \nISBN (EPUB): 978-82-303-7154-1 \nISBN (PDF):  978-82-303-7155-8',
 'The inner workings of Large Language Models Roger Gullhaug \n3 \n \n \nContents \nAbout this book ................................ ................................ ................................ .... 5 \nAbout the author ................................ ................................ ................................ .. 7 \nPart I

In [11]:
## generate the embeddings

embeddings = embedding_manager.generate_embeddings(texts)

## store in the vector db

vectorstore.add_documents(chunks, embeddings)

Generating Embedding for 1293 texts...


Batches: 100%|██████████| 41/41 [00:34<00:00,  1.19it/s]


generated embedding with shape: (1293, 384)
Adding 1293 documents to vector store...
Successfully added 1293 documents to vector store
Total documents in collection: 2564


In [12]:
## Retriever Pipeline from Vector Store

class RAGRetriever:
    """Handles query-based retrieval from the vector store"""
    
    def __init__(self, vector_store: VectorStore, embedding_manager: EmbeddingManager):
        """
        Initialize the retriever
        
        Args:
            vector_store: Vector store containing document embeddings
            embedding_manager: Manager for generating query embeddings
        """
        self.vector_store = vector_store
        self.embedding_manager = embedding_manager

    def retrieve(self, query: str, top_k: int = 5, score_threshold: float = 0.0) -> List[Dict[str, Any]]:
        """
        Retrieve relevant documents for a query
        
        Args:
            query: The search query
            top_k: Number of top results to return
            score_threshold: Minimum similarity score threshold
            
        Returns:
            List of dictionaries containing retrieved documents and metadata
        """
        print(f"Retrieving documents for query: '{query}'")
        print(f"Top K: {top_k}, Score threshold: {score_threshold}")
        
        # Generate query embedding
        query_embedding = self.embedding_manager.generate_embeddings([query])[0]
        
        # Search in vector store
        try:
            results = self.vector_store.collection.query(
                query_embeddings=[query_embedding.tolist()],
                n_results=top_k
            )
            
            # Process results
            retrieved_docs = []
            
            if results['documents'] and results['documents'][0]:
                documents = results['documents'][0]
                metadatas = results['metadatas'][0]
                distances = results['distances'][0]
                ids = results['ids'][0]
                
                for i, (doc_id, document, metadata, distance) in enumerate(zip(ids, documents, metadatas, distances)):
                    # Convert distance to similarity score (ChromaDB uses cosine distance)
                    similarity_score = 1 - distance
                    
                    if similarity_score >= score_threshold:
                        retrieved_docs.append({
                            'id': doc_id,
                            'content': document,
                            'metadata': metadata,
                            'similarity_score': similarity_score,
                            'distance': distance,
                            'rank': i + 1
                        })
                
                print(f"Retrieved {len(retrieved_docs)} documents (after filtering)")
            else:
                print("No documents found")
            
            return retrieved_docs
            
        except Exception as e:
            print(f"Error during retrieval: {e}")
            return []

rag_retriever=RAGRetriever(vectorstore,embedding_manager)

In [13]:
rag_retriever

### Integration VectorDB Context Pipeline with LLM output

In [ ]:
from langchain_groq import ChatGroq
from dotenv import load_dotenv
load_dotenv()

groq_api_key = "YOUR API KEY"

llm = ChatGroq(groq_api_key=groq_api_key, model_name = "llama-3.3-70b-versatile", temperature = 0.1, max_tokens=1024)

# simple rag function

def rag_simple(query,retriever,llm,top_k=3):
    ## retriever the context
    results=retriever.retrieve(query,top_k=top_k)
    context="\n\n".join([doc['content'] for doc in results]) if results else ""
    if not context:
        return "No relevant context found to answer the question."
    
    ## generate the answwer using GROQ LLM
    prompt=f"""Use the following context to answer the question concisely.
        Context:
        {context}

        Question: {query}

        Answer:"""
    
    response=llm.invoke([prompt.format(context=context,query=query)])
    return response.content    


In [19]:
# --- Advanced RAG Pipeline: Streaming, Citations, History, Summarization, and Memory ---
class AdvancedRAGPipeline:
    def __init__(self, retriever, llm):
        self.retriever = retriever
        self.llm = llm
        self.history = []  # Store query history

    def query(self, question: str, top_k: int = 5, min_score: float = 0.2, stream: bool = False, summarize: bool = False) -> Dict[str, Any]:
        # Retrieve relevant documents
        results = self.retriever.retrieve(question, top_k=top_k, score_threshold=min_score)
        if not results:
            answer = "No relevant context found."
            sources = []
            context = ""
        else:
            context = "\n\n".join([doc['content'] for doc in results])
            sources = [{
                'source': doc['metadata'].get('source_file', doc['metadata'].get('source', 'unknown')),
                'page': doc['metadata'].get('page', 'unknown'),
                'score': doc['similarity_score'],
                'preview': doc['content'][:700] + '...'
            } for doc in results]

            # ADDED: Include short-term chat memory
            past_context = "\n".join([
                f"Q: {h['question']}\nA: {h['answer']}"
                for h in self.history[-3:]  # last 3 interactions
            ])

            # ADDED: Updated prompt with chat history + context
            prompt = f"""You are a helpful assistant that uses both chat history and provided context to answer accurately.

Chat History:
{past_context}

Context:
{context}

Question: {question}

Answer concisely using both the chat history and the context above:"""

            # Streaming answer simulation (optional)
            if stream:
                print("\nStreaming answer...")
                for i in range(0, len(prompt), 80):
                    print(prompt[i:i+80], end='', flush=True)
                    time.sleep(0.05)
                print()

            # Run the LLM with the new prompt
            response = self.llm.invoke([prompt])
            answer = response.content

        # Add citations to answer
        citations = [f"[{i+1}] {src['source']} (page {src['page']})" for i, src in enumerate(sources)]
        answer_with_citations = answer + "\n\nCitations:\n" + "\n".join(citations) if citations else answer

        # Optionally summarize answer
        summary = None
        if summarize and answer:
            summary_prompt = f"Summarize the following answer in 2 sentences:\n{answer}"
            summary_resp = self.llm.invoke([summary_prompt])
            summary = summary_resp.content

        # Store query history (for memory)
        self.history.append({
            'question': question,
            'answer': answer,
            'sources': sources,
            'summary': summary
        })

        return {
            'question': question,
            'answer': answer_with_citations,
            'sources': sources,
            'summary': summary,
            'history': self.history
        }


adv_rag = AdvancedRAGPipeline(rag_retriever, llm)

print("\n🤖 Chatbot ready! Type your question below (type 'exit' to quit)\n")

while True:
    user_q = input("🧠 You: ").strip()
    if user_q.lower() in ['exit', 'quit']:
        print("\n👋 Goodbye, Reshu!\n")
        break

    res = adv_rag.query(user_q, top_k=3, min_score=0.1, summarize=True)

    print(f"\n📘 Bot: {res['answer']}\n")
    if res['summary']:
        print(f"📝 Summary: {res['summary']}\n")



🤖 Chatbot ready! Type your question below (type 'exit' to quit)

Retrieving documents for query: 'Appendix 1'
Top K: 3, Score threshold: 0.1
Generating Embedding for 1 texts...


Batches: 100%|██████████| 1/1 [00:00<00:00, 28.52it/s]

generated embedding with shape: (1, 384)
Retrieved 0 documents (after filtering)



📘 Bot: No relevant context found.

📝 Summary: There is no text to summarize as the provided answer states "No relevant context found." This indicates that there is no information available to create a summary.

Retrieving documents for query: 'Appendix I – GPT-OSS 120B'
Top K: 3, Score threshold: 0.1
Generating Embedding for 1 texts...


Batches: 100%|██████████| 1/1 [00:00<00:00, 29.23it/s]

...

generated embedding with shape: (1, 384)
Retrieved 1 documents (after filtering)



📘 Bot: The router chooses experts by normalizing selected scores with a softmax, creating routing weights that sum to 1, and then sends the token vector to the chosen experts, with the goal of spreading the workload evenly among all experts (experts_per_token = 4).

Citations:
[1] The Inner Workings of Large Language Models - How Neural Networks Learn Language.pdf (page 62)

📝 Summary: The router selects experts by normalizing their scores using a softmax function, which generates routing weights that add up to 1. The token vector is then sent to the chosen experts, with the aim of distributing the workload evenly among them, typically with 4 experts assigned per token (experts_per_token = 4).

Retrieving documents for query: ''
Top K: 3, Score threshold: 0.1
Generating Embedding for 1 texts...


Batches: 100%|██████████| 1/1 [00:00<00:00, 26.35it/s]

generated embedding with shape: (1, 384)
Retrieved 0 documents (after filtering)



📘 Bot: No relevant context found.

📝 Summary: There is no text to summarize as the provided answer states "No relevant context found." This indicates that there is no information available to create a summary.


👋 Goodbye, Reshu!

